In [101]:
import numpy as np
import pandas as pd
from collections import Counter
import spacy
from spacy.lang.en import English
from spacy.lemmatizer import Lemmatizer
from spacy.lookups import Lookups
import en_core_web_sm
from string import punctuation
from numpy import savetxt
nlp = en_core_web_sm.load()

In [42]:
data = pd.read_csv('Tweets.csv')
data.head()

tweet_id airline_sentiment  airline_sentiment_confidence  \
0  570306133677760513           neutral                        1.0000   
1  570301130888122368          positive                        0.3486   
2  570301083672813571           neutral                        0.6837   
3  570301031407624196          negative                        1.0000   
4  570300817074462722          negative                        1.0000   

  negativereason  negativereason_confidence         airline  \
0            NaN                        NaN  Virgin America   
1            NaN                     0.0000  Virgin America   
2            NaN                        NaN  Virgin America   
3     Bad Flight                     0.7033  Virgin America   
4     Can't Tell                     1.0000  Virgin America   

  airline_sentiment_gold        name negativereason_gold  retweet_count  \
0                    NaN     cairdin                 NaN              0   
1                    NaN    jnardino                 NaN              0   
2                    NaN  yvonnalynn                 NaN              0   
3                    NaN    jnardino                 NaN              0   
4                    NaN    jnardino                 NaN              0   

                                                text tweet_coord  \
0                @VirginAmerica What @dhepburn said.         NaN   
1  @VirginAmerica plus you've added commercials t...         NaN   
2  @VirginAmerica I didn't today... Must mean I n...         NaN   
3  @VirginAmerica it's really aggressive to blast...         NaN   
4  @VirginAmerica and it's a really big bad thing...         NaN   

               tweet_created tweet_location               user_timezone  
0  2015-02-24 11:35:52 -0800            NaN  Eastern Time (US & Canada)  
1  2015-02-24 11:15:59 -0800            NaN  Pacific Time (US & Canada)  
2  2015-02-24 11:15:48 -0800      Lets Play  Central Time (US & Canada)  
3  2015-02-24 11:15:36 -0800            NaN  Pacific Time (US & Canada)  
4  2015-02-24 11:14:45 -0800            NaN  Pacific Time (US & Canada)

In [43]:
reviews = np.array(data['text'])
labels = np.array(data['airline_sentiment'])

In [44]:
reviews

array(['@VirginAmerica What @dhepburn said.',
       "@VirginAmerica plus you've added commercials to the experience... tacky.",
       "@VirginAmerica I didn't today... Must mean I need to take another trip!",
       ...,
       '@AmericanAir Please bring American Airlines to #BlackBerry10',
       "@AmericanAir you have my money, you change my flight, and don't answer your phones! Any other suggestions so I can make my commitment??",
       '@AmericanAir we have 8 ppl so we need 2 know how many seats are on the next flight. Plz put us on standby for 4 people on the next flight?'],
      dtype=object)

In [45]:
labels

array(['neutral', 'positive', 'neutral', ..., 'neutral', 'negative',
       'neutral'], dtype=object)

In [46]:
tokenizer = nlp.Defaults.create_tokenizer(nlp)
tokenized_reviews = []
words = []
for review in reviews:
    tokens = tokenizer(review)
    tokens_list = []
    for token in tokens:
        words.append(token)
        tokens_list.append(token)
    tokenized_reviews.append(tokens_list)

In [47]:
words[:10]

[@VirginAmerica,
 What,
 @dhepburn,
 said,
 .,
 @VirginAmerica,
 plus,
 you,
 've,
 added]

In [48]:
tokenized_reviews[:100]

[[@VirginAmerica, What, @dhepburn, said, .],
 [@VirginAmerica,
  plus,
  you,
  've,
  added,
  commercials,
  to,
  the,
  experience,
  ...,
  tacky,
  .],
 [@VirginAmerica,
  I,
  did,
  n't,
  today,
  ...,
  Must,
  mean,
  I,
  need,
  to,
  take,
  another,
  trip,
  !],
 [@VirginAmerica,
  it,
  's,
  really,
  aggressive,
  to,
  blast,
  obnoxious,
  ",
  entertainment,
  ",
  in,
  your,
  guests,
  ',
  faces,
  &,
  amp,
  ;,
  they,
  have,
  little,
  recourse],
 [@VirginAmerica, and, it, 's, a, really, big, bad, thing, about, it],
 [@VirginAmerica,
  seriously,
  would,
  pay,
  $,
  30,
  a,
  flight,
  for,
  seats,
  that,
  did,
  n't,
  have,
  this,
  playing,
  .,
  ,
  it,
  's,
  really,
  the,
  only,
  bad,
  thing,
  about,
  flying,
  VA],
 [@VirginAmerica,
  yes,
  ,,
  nearly,
  every,
  time,
  I,
  fly,
  VX,
  this,
  “,
  ear,
  worm,
  ”,
  wo,
  n’t,
  go,
  away,
  :)],
 [@VirginAmerica,
  Really,
  missed,
  a,
  prime,
  opportunity,
  for,
  Men

In [57]:
def clean(words):
    nword = []
    for word in words:
        if word[0] not in punctuation and word.find('http')==-1 and any(char.isdigit() for char in word)==False:
            for pun in punctuation:
                word = word.replace(pun,' ')
                word = word.lower()
                word = word.replace(" s "," ")
            nword.append(word)
    return nword

In [49]:
reviews[:10]

array(['@VirginAmerica What @dhepburn said.',
       "@VirginAmerica plus you've added commercials to the experience... tacky.",
       "@VirginAmerica I didn't today... Must mean I need to take another trip!",
       '@VirginAmerica it\'s really aggressive to blast obnoxious "entertainment" in your guests\' faces &amp; they have little recourse',
       "@VirginAmerica and it's a really big bad thing about it",
       "@VirginAmerica seriously would pay $30 a flight for seats that didn't have this playing.\nit's really the only bad thing about flying VA",
       '@VirginAmerica yes, nearly every time I fly VX this “ear worm” won’t go away :)',
       '@VirginAmerica Really missed a prime opportunity for Men Without Hats parody, there. https://t.co/mWpG7grEZP',
       "@virginamerica Well, I didn't…but NOW I DO! :-D",
       "@VirginAmerica it was amazing, and arrived an hour early. You're too good to me."],
      dtype=object)

In [65]:
def lemma(sentence):
    doc = nlp(sentence)
    sent = " ".join([token.lemma_.lower() for token in doc if token.is_stop==False])
    return sent

In [66]:
rev = []
for re in reviews:
    re = lemma(re)
    re = re.split()
    rn = clean(re)
    rev.append(rn)
rev

[['say'],
 ['plus', 'add', 'commercial', 'experience', 'tacky'],
 ['today', 'mean', 'need', 'trip'],
 ['aggressive',
  'blast',
  'obnoxious',
  'entertainment',
  'guest',
  'face',
  'amp',
  'little',
  'recourse'],
 ['big', 'bad', 'thing'],
 ['seriously',
  'pay',
  'flight',
  'seat',
  'playing',
  'bad',
  'thing',
  'fly',
  'va'],
 ['yes', 'nearly', 'time', 'fly', 'vx', 'ear', 'worm', 'will', 'away'],
 ['miss', 'prime', 'opportunity', 'men', 'hats', 'parody'],
 ['didn t', '…'],
 ['amazing', 'arrive', 'hour', 'early', 'good'],
 ['know', 'suicide', 'second', 'leading', 'cause', 'death', 'teen'],
 ['pretty', 'graphic', 'well', 'minimal', 'iconography'],
 ['great', 'deal', 'think', 'trip', 'amp', 'go', 'trip', 'p'],
 ['fly', 'fabulous', 'seductive', 'sky', 'u', 'stress', 'away', 'travel'],
 ['thank'],
 ['sfo', 'pdx', 'schedule', 'mia'],
 ['excited',
  'cross',
  'country',
  'flight',
  'lax',
  'mco',
  'hear',
  'great',
  'thing',
  'virgin',
  'america'],
 ['fly',
  'nyc',
  '

In [68]:
words = []
for review in rev:
    for word in review:
        words.append(word)

In [72]:
counts = Counter(words)
vocab = sorted(counts, key=counts.get, reverse=True)
vocab_to_int = {word: cnt for cnt, word in enumerate(vocab, 1)}
reviews_ints = []
for review in rev:
    reviews_ints.append([vocab_to_int[word] for word in review])

In [73]:
reviews_ints

[[40],
 [352, 161, 962, 74, 4573],
 [33, 195, 16, 78],
 [2695, 1997, 3316, 698, 1508, 770, 17, 305, 1998],
 [260, 29, 152],
 [263, 61, 1, 21, 4574, 29, 152, 11, 1414],
 [73, 1054, 6, 11, 1648, 3317, 4575, 100, 283],
 [38, 2291, 1120, 4576, 3318, 4577],
 [3319, 450],
 [202, 124, 3, 94, 25],
 [31, 1790, 342, 1791, 270, 1055, 1649],
 [448, 3320, 102, 4578, 4579],
 [46, 200, 85, 78, 17, 24, 78, 1999],
 [11, 1415, 4580, 771, 49, 1180, 283, 48],
 [2],
 [182, 871, 215, 566],
 [811, 506, 550, 1, 128, 478, 166, 46, 152, 625, 812],
 [11, 299, 182, 93, 1792, 53, 21, 872, 3321, 7],
 [587, 185, 11, 1327, 185, 451],
 [31, 3322, 167, 230, 343, 47, 11],
 [360, 6, 772, 21, 188, 567],
 [62, 3320],
 [62, 4581, 2292, 241, 25, 963],
 [107, 4582, 413, 183, 3323, 1416, 274],
 [35, 433, 1001, 1002, 21, 210, 35, 89, 21, 283, 551, 47, 155, 843],
 [186, 747, 662, 588, 93, 65, 60, 83],
 [109, 271, 2293, 272, 169, 271, 203, 31, 100, 172, 873, 81, 138],
 [38, 427, 274],
 [202, 507, 132, 3324, 4583, 2696, 2697, 4584

In [109]:
encoded_label = []
for label in labels:
    if label == "negative":
        encoded_label.append(0)
    elif label == "neutral":
        encoded_label.append(1)
    else:
        encoded_label.append(1)
encoded_review = reviews_ints

In [110]:
review_lens = Counter([len(x) for x in encoded_review])
print("Zero-length reviews: {}".format(review_lens[0]))
print("Maximum review length: {}".format(max(review_lens)))

Zero-length reviews: 70
Maximum review length: 43


In [111]:
print('Number of reviews before removing outliers: ', len(encoded_review))
non_zero_idx = [x for x, review in enumerate(encoded_review) if len(review) != 0]
encoded_review = [encoded_review[x] for x in non_zero_idx]
classes = np.array([encoded_label[x] for x in non_zero_idx])
print('Number of reviews after removing outliers: ', len(encoded_review))

Number of reviews before removing outliers:  14640
Number of reviews after removing outliers:  14570


In [112]:
for i in range(14640):
    print(encoded_review[i]," : ",encoded_label[i])

[40]  :  1
[352, 161, 962, 74, 4573]  :  1
[33, 195, 16, 78]  :  1
[2695, 1997, 3316, 698, 1508, 770, 17, 305, 1998]  :  0
[260, 29, 152]  :  0
[263, 61, 1, 21, 4574, 29, 152, 11, 1414]  :  0
[73, 1054, 6, 11, 1648, 3317, 4575, 100, 283]  :  1
[38, 2291, 1120, 4576, 3318, 4577]  :  1
[3319, 450]  :  1
[202, 124, 3, 94, 25]  :  1
[31, 1790, 342, 1791, 270, 1055, 1649]  :  1
[448, 3320, 102, 4578, 4579]  :  1
[46, 200, 85, 78, 17, 24, 78, 1999]  :  1
[11, 1415, 4580, 771, 49, 1180, 283, 48]  :  1
[2]  :  1
[182, 871, 215, 566]  :  0
[811, 506, 550, 1, 128, 478, 166, 46, 152, 625, 812]  :  1
[11, 299, 182, 93, 1792, 53, 21, 872, 3321, 7]  :  0
[587, 185, 11, 1327, 185, 451]  :  1
[31, 3322, 167, 230, 343, 47, 11]  :  1
[360, 6, 772, 21, 188, 567]  :  0
[62, 3320]  :  1
[62, 4581, 2292, 241, 25, 963]  :  1
[107, 4582, 413, 183, 3323, 1416, 274]  :  1
[35, 433, 1001, 1002, 21, 210, 35, 89, 21, 283, 551, 47, 155, 843]  :  0
[186, 747, 662, 588, 93, 65, 60, 83]  :  0
[109, 271, 2293, 272, 169

[101, 780, 91, 28, 1124, 23, 23, 191]  :  0
[2, 18, 19, 487]  :  0
[152, 49, 35, 144, 463, 3458, 1]  :  0
[1072, 546, 545, 138, 13, 54, 4872, 43, 70, 120, 49, 31, 80, 49, 330, 208]  :  1
[516, 4873, 76, 969, 385, 64, 31, 16, 47, 287, 453, 193]  :  0
[531, 405, 1443, 125, 340, 106, 19, 273, 103, 340, 100, 241, 1550]  :  0
[750, 1684, 85, 10, 55, 50, 41, 284, 216, 8]  :  1
[2782, 90, 60, 39, 150, 1286, 106]  :  0
[750, 78, 793, 211, 3459, 342, 3460, 21, 61, 392]  :  1
[619, 23, 6, 56, 333, 41, 1845, 350]  :  1
[101, 64, 31, 10, 1, 2061, 4874]  :  1
[874, 2357, 37, 134, 61, 4875, 47, 505, 17, 522, 418]  :  0
[2, 69, 179, 251, 32, 10, 47, 214]  :  1
[3461, 29, 8, 4, 105, 109, 200, 1444, 229, 69]  :  0
[1445, 1, 2358, 5, 34, 1, 1287, 72, 3, 14]  :  0
[2, 339, 7, 1446, 83, 580, 281]  :  0
[29, 340, 4876, 1843, 57, 207, 1]  :  0
[32, 31, 24, 748, 1, 148]  :  0
[61, 66, 370, 124, 13, 934, 19, 856]  :  0
[120, 58, 241, 32, 15, 1354, 153, 160, 43, 138]  :  1
[46, 22, 587, 185]  :  0
[1347, 10, 4

[212, 1887, 1, 129, 147, 67, 5133, 5134, 5135, 2]  :  0
[370, 2, 107, 103, 124, 5136]  :  1
[16, 910, 318, 26, 1, 5, 1, 903]  :  0
[145, 2848, 117, 291, 3574, 8, 4, 95, 5137, 75, 177]  :  0
[22, 23, 180, 483, 498, 344, 14, 6, 115]  :  1
[59, 255, 48, 1682]  :  1
[70, 34, 1, 651, 1, 41, 617, 1]  :  1
[2, 5138, 1446, 83, 365, 57]  :  0
[2]  :  0
[25, 1020, 346, 1888, 3575, 487]  :  1
[2849, 79, 181, 1587, 216, 1054, 2127]  :  1
[6, 863, 5139, 5140, 3572]  :  0
[22, 222, 2421, 55, 110, 645, 1080, 2850, 800]  :  0
[71, 3, 292]  :  1
[15, 14, 5141, 5142, 5143]  :  0
[12, 5144]  :  0
[1098, 10, 555, 1098, 10, 23, 67, 376, 614]  :  0
[1542, 2, 142, 1, 2851, 243, 12, 56, 9, 480]  :  0
[5145, 20, 64]  :  0
[6, 580, 186, 332, 198, 1889]  :  0
[2, 366, 13, 1890, 67]  :  0
[196, 1, 5, 790, 1372, 38, 98, 45, 100, 64, 20]  :  0
[24, 54, 13, 14, 5146, 20, 5147]  :  1
[1, 81, 5, 279, 336, 429, 34, 1, 72, 641, 13, 1374, 5148, 1045, 20, 36]  :  0
[58, 24, 38, 98, 77, 13, 6, 182, 257, 263, 49, 70, 20]  :

[73, 148, 122, 123, 79, 181, 8, 4, 168, 163, 123, 202, 39, 36]  :  0
[144, 1185, 1, 826, 3673, 5390, 144, 5391, 5392, 3674, 69, 408, 5393]  :  0
[2, 417]  :  0
[642, 2163, 3675, 346, 247, 3676, 689]  :  1
[90, 68, 28]  :  1
[2066, 13, 57, 404, 171, 8, 4, 1081, 13, 6, 2, 171]  :  0
[73, 149, 631, 1725, 2]  :  0
[1, 1299, 5394, 310, 182, 53, 549, 97, 1106, 932, 425, 22]  :  0
[2]  :  0
[297, 38, 1347, 1, 125, 207, 39]  :  0
[40, 796, 772, 132, 136, 47, 10, 181, 402, 199, 47, 521]  :  1
[263, 81, 10, 311, 937, 5395, 1031, 363, 141, 9, 327, 158, 179, 3677, 235]  :  0
[198, 1, 74, 109, 86, 1, 5, 81, 737, 38, 1, 1206]  :  0
[10, 181, 47, 5396]  :  1
[138, 5397, 33, 1360, 2917, 749, 1734, 1181]  :  1
[2918, 953, 44, 953, 2474, 2919, 2920, 42, 2130, 1439]  :  0
[210, 48, 33, 12, 66, 1998, 190, 204, 521, 734]  :  1
[12, 3678, 338, 248, 18, 337, 1, 18]  :  1
[42, 248, 368, 1, 20, 211, 1198, 866, 256, 18, 1]  :  0
[564, 410, 477, 653, 975, 154, 1735, 2475, 7, 1735]  :  0
[2916, 57]  :  0
[168, 16

[1, 131, 146, 5683, 5684, 1, 1131, 3790, 818, 333]  :  0
[32, 69, 7, 219, 724, 154, 519, 58, 590, 20, 5685]  :  0
[481, 2192, 107, 494]  :  0
[859, 251, 83, 1748]  :  0
[212, 43, 5686, 1625, 1, 1210, 323, 606, 484, 77, 71, 27, 70]  :  1
[5, 159, 536, 1061, 756, 782, 685, 139, 95, 79, 5687, 2483]  :  0
[29, 1, 131, 32, 764, 1239, 5688, 2802]  :  1
[1199, 1660, 2109, 1344, 2995, 9, 30, 1, 47, 214]  :  1
[2511, 49, 136, 233]  :  0
[205, 106, 22, 1286, 106, 751, 490, 413, 1541]  :  1
[1837, 418, 29, 516, 830, 387, 57, 2469, 14, 2996, 34, 1]  :  0
[1007, 46, 8, 4, 482, 182, 2824, 1146]  :  0
[5689, 19, 412, 1286, 490, 29, 990, 35]  :  0
[1650, 247, 271, 8, 4, 19, 83, 1467, 1286]  :  1
[1484, 2, 119]  :  1
[109, 22, 89, 1, 150, 5690, 105]  :  0
[2, 44, 225, 205, 81, 240, 658, 11, 526, 21, 3791, 206, 1242]  :  0
[36, 5691, 5692, 901, 1552, 23, 1397, 868, 16, 5693, 483, 1368]  :  0
[223, 245, 386, 129, 147, 48, 259, 533, 3362, 473]  :  0
[353, 72, 5694, 157, 5695, 3792, 5696]  :  0
[2, 1494, 4

...

[234, 8759, 4434, 562, 150, 14, 301, 57, 1, 81]  :  0
[15, 3, 158, 282, 840, 1119, 112, 496, 54, 17, 321]  :  0
[73, 1, 131, 636, 687, 1515, 2188, 1654, 8760, 1523]  :  0
[290, 37, 18, 881, 10, 6, 1909]  :  0
[2, 21, 889, 2240, 1, 3748, 102]  :  0
[2, 42, 10, 2, 156, 67, 589]  :  0
[518, 21, 2186, 80, 31, 158, 1]  :  0
[35, 50, 4, 36, 20, 367, 58, 38, 98]  :  0
[225, 3, 15]  :  0
[1, 124, 34, 1, 43, 80, 98]  :  0
[6, 27, 10, 8761, 778, 97, 79, 88, 186, 8762]  :  1
[563, 123, 376, 102, 42]  :  0
[373, 1, 14, 148, 1784, 98, 474]  :  0
[12, 56, 3, 192, 394, 41, 140, 8763, 373]  :  0
[18, 19, 111, 945]  :  0
[169, 53, 2187, 45, 13, 338, 149]  :  0
[19, 3, 15, 19, 144, 988, 1, 149, 29, 4]  :  0
[18, 19, 6, 112, 8764, 440, 1076, 229, 7]  :  0
[217, 2012, 17, 144, 313, 1, 352, 26, 1, 853]  :  0
[320]  :  0
[2, 491, 146, 341, 190, 17, 275, 12, 440, 697, 1156]  :  1
[1, 33, 280, 6, 91, 172, 27, 65, 17, 23, 9, 30, 15, 296, 151, 7]  :  0
[63, 620, 88, 12, 2509]  :  0
[19, 307, 28, 251, 164]  :  1

[3257, 19, 1, 26, 20, 36, 40]  :  0
[1, 42]  :  1
[302, 1829, 42, 41, 38, 1, 1951, 189, 18, 2250, 88, 296, 13]  :  1
[2]  :  0
[92, 579, 2603, 294, 661, 1140, 3263, 4504, 1494, 63, 4505]  :  0
[51, 1136]  :  0
[138, 1, 548, 53, 13, 1, 131, 2287, 25]  :  0
[324, 13, 6, 104, 23, 19, 28, 298]  :  0
[216, 337, 135, 976, 1]  :  1
[24, 464, 1369, 2692, 2288, 491, 106]  :  0
[1, 145, 9, 82, 2198, 3006, 24]  :  0
[1, 114, 1701, 42, 871, 52, 9, 82, 7]  :  1
[57, 339, 2175, 757, 34, 1, 20, 36, 3]  :  0
[179, 1, 19, 24, 306, 205, 2285, 4506, 578]  :  0
[103, 232, 2005]  :  0
[675, 1, 131, 1438, 3057]  :  0
[26, 176, 313, 63, 39, 8881]  :  0
[137, 438, 2]  :  0
[814, 362, 57, 1369, 2692, 2288, 2, 245, 14]  :  1
[555]  :  0
[89, 309, 6, 59, 1742, 8, 4, 87, 55, 10, 1465, 207]  :  0
[1057, 103, 405, 1580, 1944, 3661, 92, 3066, 1105, 557, 8882]  :  0
[62, 394, 344, 46, 719]  :  1
[2]  :  1
[171, 346, 74, 278, 348, 533]  :  0
[251, 91, 1517, 1001, 188, 920, 268, 245, 21, 1754, 6, 337]  :  1
[2412, 54, 

[2, 49, 351, 83, 55, 9169, 24, 997, 3254]  :  0
[10, 744, 6, 27, 881, 10, 309, 112]  :  0
[824, 4507, 12, 325, 3, 2434, 4508, 653, 9, 1, 91, 172, 7]  :  0
[6, 11, 226]  :  0
[15, 42, 196]  :  1
[655, 72, 121, 33, 9170, 9171, 62, 63, 25, 37, 87]  :  1
[1, 43, 224, 86, 3571, 18, 375, 5, 1, 24]  :  0
[113, 63, 1970, 308, 875, 249, 27, 293, 3062]  :  0
[4514]  :  0
[18, 3085, 12, 395, 681, 978, 248, 40, 2694, 111, 450]  :  0
[119, 46, 8, 4, 4, 36, 111, 113, 2775, 242]  :  0
[31, 372, 1253, 272, 344, 1732]  :  1
[2, 119, 14, 54, 20]  :  0
[35, 2615, 2553, 76, 15, 3]  :  0
[15, 41, 99, 1, 1, 61, 536, 176, 26, 1]  :  1
[137, 58, 410, 37, 1172, 408, 9172, 265, 1102, 9173, 2124, 9174]  :  1
[1198, 866]  :  1
[24, 26, 52, 517, 9175, 100, 172, 43, 41]  :  0
[62, 14, 90, 202, 9176]  :  0
[9177, 2598, 1573, 122, 11, 170, 566, 373, 41]  :  0
[1, 26, 132, 5, 270, 38, 98, 21, 34, 116]  :  0
[85, 93, 13, 6, 171, 55, 8]  :  1
[42, 196, 8, 4, 224, 1591, 476, 473, 9, 1, 1, 17, 15, 19]  :  0
[2038, 1798, 1

[87, 24, 149, 2671, 1505, 8, 4, 100, 97, 2216, 28]  :  0
[326, 8, 4, 610]  :  1
[12, 102, 80, 145, 213, 22, 9386, 9387]  :  1
[16, 123, 341, 190, 1, 9, 30, 658, 15, 3]  :  0
[64, 263, 3139]  :  1
[85, 1143, 294, 58, 177, 561, 87]  :  1
[13, 3, 146, 26, 1]  :  1
[20, 36, 38, 158, 1, 752, 335, 216, 8, 9388, 64, 435]  :  1
[267]  :  1
[154, 49, 16, 23, 80, 24, 96, 13, 1, 433]  :  1
[139, 36, 673, 869, 797, 4563]  :  0
[263, 47, 13, 3, 1, 1143, 217, 716]  :  0
[20, 36, 114, 20, 791, 115, 198, 406, 669, 26, 9389]  :  1
[1509, 10, 24, 265, 189, 3, 3525, 9390, 4564]  :  0
[1216, 427, 24, 56, 259, 456, 51, 196, 29]  :  0
[2628, 125, 150, 44, 1, 88, 400, 9391, 7, 9392, 1]  :  0
[73, 2, 27, 2484, 12, 17, 993, 11, 52, 374]  :  0
[29, 22, 48, 29, 9393, 9394]  :  0
[46, 1, 74, 182, 96, 3225, 1457, 395, 1097, 4275, 22, 35]  :  0
[448, 29, 114, 101, 1, 498, 180, 4564, 812, 22, 1088]  :  1
[46, 2]  :  0
[73, 785, 162, 287, 1347, 300, 207, 1, 1168, 1859, 9395]  :  0
[12, 65, 65, 325, 9396, 1137, 9397, 

IndexError: list index out of range

In [113]:
def pad_features(reviews_ints, seq_length):
    features = np.zeros((len(reviews_ints), seq_length), dtype=int)
    for i, row in enumerate(reviews_ints):
        features[i, -len(row):] = np.array(row)[:seq_length]
    return features

In [114]:
seq_length = 42
features = pad_features(encoded_review, seq_length=seq_length)
encoded_review = features
encoded_label = classes

In [105]:
for i in range(len(encoded_review)):
    print(encoded_review[i]," : ",encoded_label[i])

[ 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0 40]  :  2
[   0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0  352  161  962   74 4573]  :  4
[  0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0   0  33 195  16  78]  :  2
[   0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0 2695 1997 3316  698 1508  770   17  305 1998]  :  0
[  0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0   0   0 260  29 152]  :  0
[   0    0    0    0    0    0    0    0    0    0    0    0    0    

 0 0 0 0 5]  :  0
[   0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0  444   45   15  363    4   16  161 1339  416   76]  :  0
[   0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0  161 3366  206  364 1525 2018  157 3391 1526]  :  2
[   0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0  632  541 1531  345  216 4730   63  134]  :  4
[   0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    1
  129  147  342    1   93 4731  265  223   47 1431 1016  571   62   35]  :  4
[   0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0 

    0    0    0    0    0    0    0   27  186  181   24  254 1363  497]  :  0
[   0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    1    5  387 1701  270   38   98  382 1562    7]  :  0
[   0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
  534  312  149 4982   57   61   42 1702    1    9    1   43  507  393]  :  0
[   0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0  438 3492   37 2067   22  318 2386]  :  0
[  0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   8 106  60
  28 168 123  57 322 982]  :  0
[   0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0   

 619 223  22 433  42  78]  :  0
[   0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0  634 3562   47 1140  594   20   27  193]  :  0
[   0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0   94 2840   25   22]  :  4
[   0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0   10   43   14 1867   46   31  274  148  206   64   13   45  133]  :  0
[   0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0 5114  398    8    4 5115   95   23   80]  :  0
[   0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0  

 743 476  14  53   3   5]  :  0
[  0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0   0   0 555 106 569]  :  0
[   0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0   19  113 1909  221  302   21   47  395]  :  0
[   0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0  242  201    6  817 1532 1424    6    6 1349  251]  :  2
[   0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0  359 1090  199  166   90   68  445 5292]  :  4
[   0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    

...

    0    0    0    0    0    0  397  218 1057  758  414   11  809  557]  :  2
[   0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0  342 1149 3593]  :  2
[  0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0 103 758 661  51 274]  :  2
[  0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0  93 247   8
 660 232   6   7 262   2]  :  0
[  0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0 604
 255 288 809 557 254  48]  :  2
[   0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0 

    0    0    0    0    0    0    0    0  157  912  175   11   22 2910]  :  2
[   0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0  490   53 3304   14   33  301  105  654 1021  392]  :  0
[0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 2]  :  4
[   0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0 9076    1    5 1850  566   38 9077  474   16   21    1  474]  :  0
[  0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0   0  29   4 381  41]  :  0
[   0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0   16  437    8    4 4380  276    8    

    0    0    0   18   81  351   36   26  688 3265    9    1 2693 9159]  :  0
[   0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0  252   55   66  235 9160 9161]  :  0
[   0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0   46  228   46    4 2404  533  557  473]  :  4
[   0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0   70  527   66  447 1350   78 1702   19   66]  :  0
[   0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0  427   71   25  106 1770 1868]  :  0
[   0    0    0    0    0    0    0    0  

  51  16  26  76  11 206]  :  2
[   0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0   62   36   28 1119  112  111]  :  0
[   0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0   65 1698    1    9 9307    1    9   30  431   65  488]  :  0
[  0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0   0   0   0 233  68]  :  2
[   0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    2   29   74   22   92 2181   22  791]  :  0
[   0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    

   1  53 114  13  79 389]  :  0
[  0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0  18   6 567
  21 928 188 268 205  21]  :  0
[   0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0   16 2583    7    1 9478 9479 9480]  :  0
[   0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0 9481   24]  :  2
[  0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0  47 288 617  41 110]  :  0
[   0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0  163    2

In [115]:
savetxt('encoded_review.csv',encoded_review,delimiter=',')
savetxt('encoded_label.csv',encoded_label,delimiter=',')

In [116]:
print(len(encoded_review))
print(len(encoded_label))

14570
14570


In [108]:
len(vocab)

9647